# Libraries and input parameters

In [1]:
# LIBRARIES #

import numpy as np
import pydicom as dcm
from scipy import ndimage

import SimpleITK as sitk

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import LinearColorMapper, BasicTicker, ColorBar, Plot, CustomJS, ColumnDataSource, Rect
from bokeh.layouts import row, gridplot, column
from bokeh.models.widgets import Slider, Button
from bokeh.events import ButtonClick


output_notebook()

Loading BokehJS ...

In [2]:
# INPUT PARAMETERS #
#m_filename = 'colli5_72dpi.tif'

#m_path = 'G:/Commun/PHYSICIENS/DQPRM/2018-2020/Mesures/film/Film Erwann/20190731/FilmTestEscalier/24h/'
#m_filename = 'scann'
m_path="//interne.o-lambret.fr/oscar/RP/Commun/PHYSICIENS/Erwann/cyber M6/mesures Antoine/Choteau/Choteau bananas nominal DQA/gaf/test recalage/"
m_filename = 'scan1-'
m_nbOfFiles = 5
m_firstNb = 1

m_imgPlotWidth = 500
m_threshold = 45000

# coefs R/B gray values:
m_coefX6 = 164192    #x6
m_coefX5 = -1141014  #x5
m_coefX4 = 3299431   #x4
m_coefX3 = -5085544  #x3
m_coefX2 = 4411686   #x2
m_coefX1 = -2046039  #x
m_coefX0 = 397570    #
m_RBmax = 1.40       # maximum R/B value over which the dose is not calculated
m_RBmin = 0.80       # minimum R/B value below which the dose is not calculated

'''# coefs R/B DO:
m_coefX6 = 0   #x6
m_coefX5 = 0  #x5
m_coefX4 = 0   #x4
m_coefX3 = 1774.1  #x3
m_coefX2 = -3907.8   #x2
m_coefX1 = 3276.7  #x
m_coefX0 = -935.12  '''


m_dosemax = 1000.0 #cGy

# Gafchromic film Class

In [3]:
# GAFCHROMIC FILMS CLASS #

class GafchromicFilms:
    
    # Constructor
    #  filename: gafchromic tiff file to read
    def __init__(self, filename):
        self.sizex, self.sizey, self.img_origin, self.img_spacing, self.array = self.readImg(filename)
    
    # Reads the image
    #  filename: filename of the gafchromic tiff file to read
    def readImg(self,filename):
        img = sitk.ReadImage(filename)
        sizex = img.GetWidth()
        sizey = img.GetHeight()
        imgOrigin = img.GetOrigin()
        imgSpacing = img.GetSpacing()
        array = sitk.GetArrayFromImage(img)
        return sizex, sizey, imgOrigin, imgSpacing, array
  
    
    # sets the median image of a series of images in array
    # path: directory where the images are saved
    # filename: filename the dose imgs
    # nbOfImgs: nb of imgs to use
    def medianImage(self, path, filename, nbOfImgs, firstNb):
        imgs = []
        for i in range(nbOfImgs):
            im = sitk.ReadImage(path+filename+str(i+firstNb)+'.tif')
            ar = sitk.GetArrayFromImage(im)
            imgs.append(ar)

        # creation and filling of median image:
        medianImg = np.empty((self.sizey,self.sizex,3))
        for i in range(self.sizex):
            for j in range(self.sizey):
                for k in range(3):
                    a = []
                    for l in range(nbOfImgs):
                        a.append(imgs[l][j][i][k])
                    medianImg[j][i][k] = np.median(a)
                    #medianImg[j][i][k] = np.mean(a)
        self.array = medianImg
    
        return medianImg

    
    # Converts the gafchromic image to dose using the optical density of red over blue channels and a polynomial 
    #  conversion curve (4th degree)
    #  coefs: calibration curve coefficients
    #  dosemax: maximum dose over which the dose is not calculated
    def convertToDose_polynomeLogRB(self, coefs, rbmin, rbmax, dosemax):
        # replaces every 65535 value in array with 65534 to avoid division by zero:
        self.array[self.array==65535]=65534
        
        # converts in optical density
        dor = -np.log10(self.array[:,:,0]/65535.0)
        dob = -np.log10(self.array[:,:,2]/65535.0)
    
        # red channel over blue channel:
        rsb = dor/dob
        rsb[rsb<rbmin] = rbmin
        rsb[rsb>rbmax] = rbmax
        
        # converting in dose:
        doseimg = coefs[0]*rsb**6 + coefs[1]*rsb**5 + coefs[2]*rsb**4 + coefs[3]*rsb**3 + coefs[4]*rsb**2 + coefs[5]*rsb + coefs[6]
        doseimg[doseimg>dosemax] = dosemax
        doseimg[doseimg<0] = 0
        
        return doseimg
    
    
    # Converts the gafchromic image to dose using the red over blue pixel values and a polynomial 
    #  conversion curve (3rd degree)
    #  coefs: calibration curve coefficients
    #  dosemax: maximum dose over which the dose is not calculated
    def convertToDose_polynomeGreyValueRB(self, coefs, rbmin, rbmax, dosemax):
        # replaces every 65535 value in array with 65534 to avoid division by zero:
        self.array[self.array==65535]=65534
        
        # red channel over blue channel:
        rsb = self.array[:,:,0]/self.array[:,:,2]
        rsb[rsb<rbmin] = rbmin
        rsb[rsb>rbmax] = rbmax
        
        # converting in dose:
        doseimg = coefs[0]*rsb**6 + coefs[1]*rsb**5 + coefs[2]*rsb**4 + coefs[3]*rsb**3 + coefs[4]*rsb**2 + coefs[5]*rsb + coefs[6]
        doseimg[doseimg>dosemax] = dosemax
        doseimg[doseimg<0] = 0
        
        return doseimg
    
    
    # Saves the dose image to a tiff file that can be read using Verisoft
    # doseimg: img to save
    # filename: filename the dose img will be written to
    def saveToTiff(self, doseimg, filename):
        imagetif = sitk.Image([doseimg.shape[1],doseimg.shape[0]], sitk.sitkVectorUInt16, 3)
        imagetif.SetSpacing(self.img_spacing)
        imagetif.SetOrigin(self.img_origin)
        for j in range(0, doseimg.shape[0]):
            for i in range(0, doseimg.shape[1]):
                a = int(doseimg[j,i])
                imagetif.SetPixel(i,j,[a, a, a])
        
        writer = sitk.ImageFileWriter()
        writer.SetFileName(filename)
        writer.Execute(imagetif)
        return True
    

# Interface definition

In [6]:
# PLOTS IMAGE AND PROFILES #
# @params:
#   img: array img to display
#   sizex: size of the img in x
#   sizey: size of the img in y
#   imgPlotWidth: width of the image plot

def displayImage(img, sizex, sizey, imgPlotWidth):

    # Displays the dose image (p1):

    maxdose = int(np.amax(doseimg))

    color_mapper = LinearColorMapper(palette="Viridis256", low=0, high=maxdose)

    color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, location=(0,0),
                     title='Dose cGy')

    p1 = figure(plot_width=int(imgPlotWidth*1.1), plot_height=int(imgPlotWidth*sizey/sizex), 
                    x_range=(0,sizex), y_range=(0,sizey), 
                    title="Dose image", toolbar_location="above")

    l1_source = ColumnDataSource(data=dict(x=[0,int(sizex)], y=[int(sizey/2),int(sizey/2)]))
    l2_source = ColumnDataSource(data=dict(x=[int(sizex/2), int(sizex/2)], y=[0, int(sizey)]))

    p1.image(image=[doseimg], x=[0], y=[0], dw=[sizex], dh=[sizey], color_mapper=color_mapper)
    p1.line('x', 'y', source=l1_source, line_width=2, line_color=(255, 255, 255, 0.7))
    p1.line('x', 'y', source= l2_source, line_width=2, line_color=(255, 255, 255, 0.7))

    p1.add_layout(color_bar, 'right')


    # Displays the zoomed window:
    p1b_source = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

    jscode="""
        var data = source.data;
        var start = cb_obj.start;
        var end = cb_obj.end;
        data['%s'] = [start + (end - start) / 2];
        data['%s'] = [end - start];
        source.change.emit();
    """

    p1.x_range.callback = CustomJS(args=dict(source=p1b_source), code=jscode % ('x', 'width'))
    p1.y_range.callback = CustomJS(args=dict(source=p1b_source), code=jscode % ('y', 'height'))

    p1b = figure(title='Zoom Window', plot_width=int(imgPlotWidth*0.5), 
                     plot_height=int(imgPlotWidth*0.5*sizey/sizex), 
                     x_range=(0,sizex), y_range=(0,sizey), tools='')
    p1b.image(image=[doseimg], x=[0], y=[0], dw=[sizex], dh=[sizey], color_mapper=color_mapper)
    rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
                    line_color='white', fill_color='white')
    p1b.add_glyph(p1b_source, rect)

    p1b.xaxis.major_tick_line_color = None  # turn off x-axis major ticks
    p1b.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks
    p1b.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
    p1b.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
    p1b.xaxis.major_label_text_color = None  # turn off x-axis tick labels leaving space
    p1b.yaxis.major_label_text_color = None  # turn off y-axis tick labels leaving space 

    # Displays profiles:
    maxdose_x = np.amax(doseimg[:,:])
    p2_source = ColumnDataSource(data=dict(x=np.arange(0, sizex, 1), y=doseimg[int(sizey/2)]))
    p2 = figure(plot_width=480, plot_height=300, x_range=(0,sizex), y_range=(0,maxdose_x), 
                    title="Horizontal dose profile", toolbar_location="above")
    p2.line('x', 'y', source=p2_source, line_color="#2690d4", line_width=3, line_alpha=1.0)

    p3 = figure(plot_width=480, plot_height=300, x_range=(0,sizey), y_range=(0,maxdose_x), 
                    title="Vertical dose profile", toolbar_location="above")
    p3_source = ColumnDataSource(data=dict(x=np.arange(0, sizey, 1), y=doseimg[:,int(sizex/2)]))
    p3.line('x', 'y', source=p3_source, line_color="#2690d4", line_width=3, line_alpha=1.0)


    # Callback functions called when the sliders are changed
    callback1 = CustomJS(args=dict(source1=l1_source, source2=p2_source), code="""
        var f = horizontalPosSlider.value;

        var data1 = source1.data;
        var y1 = data1['y'];
        y1[0] = f;
        y1[1] = f;
        source1.change.emit();

        var data2 = source2.data;
        var x2 = data2['x'];
        var y2 = data2['y'];
        for (i = 0; i < x2.length; i++) {
            y2[i] = img[f][i];
        }    
        source2.change.emit();
    """)


    callback2 = CustomJS(args=dict(source1=l2_source, source2=p3_source), code="""
        var f = verticalPosSlider.value;

        var data1 = source1.data;
        var x1 = data1['x'];
        x1[0] = f;
        x1[1] = f;
        source1.change.emit();
    
        var data2 = source2.data;
        var x2 = data2['x'];
        var y2 = data2['y'];
        for (i = 0; i < x2.length; i++) {
            y2[i] = img[i][f];
        }    
        source2.change.emit();
    """)

    # Button Callbacks:
    saveCallback = CustomJS(code="""
        console.log("hello");
    """)


    # plotting inline:
    slider1 = Slider(start=0, end=sizey, value=int(sizey/2), step=1, title="Horizontal line position", callback=callback1)
    callback1.args["horizontalPosSlider"] = slider1
    callback1.args["img"] = doseimg

    slider2 = Slider(start=0, end=sizex, value=int(sizex/2), step=1, title="Vertical line position", callback=callback2)
    callback2.args["verticalPosSlider"] = slider2
    callback2.args["img"] = doseimg

    crop_button = Button(label="Crop Image", button_type="default")

    save_button = Button(label="Save Image To TIFF", button_type="default", callback=saveCallback)
    saveCallback.args["img"] = doseimg
    saveCallback.args["folder"] = m_path

    # Organizing the graphs:
    grid = gridplot([[p1,column(p1b,crop_button,save_button)],[slider1,slider2],[p2, p3]])

    show(grid)

# Main prgm

In [8]:
# CALCULATES THE DOSE IMAGE #

coefs = [m_coefX6, m_coefX5, m_coefX4, m_coefX3, m_coefX2, m_coefX1, m_coefX0]

#print(m_path+m_filename+str(m_firstNb)+'.tif')
film1 = GafchromicFilms(m_path+m_filename+str(m_firstNb)+'.tif')
film2 = GafchromicFilms(m_path+'scan2-'+str(m_firstNb)+'.tif')


#medianimg = film.medianImage(m_path, m_filename, m_nbOfFiles, m_firstNb)
#doseimg = film.convertToDose_polynomeGreyValueRB(coefs, m_RBmin, m_RBmax, m_dosemax)
#film.saveToTiff(doseimg, m_path+'medianDose.tif')


# binarization of the images to see contours and holes:
doseimg1 = film1.array[:,:,0]
#doseimg[doseimg<m_threshold] = 0
#doseimg[doseimg>=m_threshold] = 1
doseimg1[doseimg1<60000] = 0
doseimg1[doseimg1>=60000] = 1

doseimg2 = film2.array[:,:,0]
doseimg2[doseimg2<60000] = 0
doseimg2[doseimg2>=60000] = 1


# Initial transform:
fixedimg = sitk.Image(film1.sizex, film1.sizey, sitk.sitkFloat32)
for i in range(film1.sizex):
    for j in range(film1.sizey):
        fixedimg.SetPixel(i, j, float(doseimg1[j,i]))

movingimg = sitk.Image(film2.sizex, film2.sizey, sitk.sitkFloat32)
for i in range(film2.sizex):
    for j in range(film2.sizey):
        movingimg.SetPixel(i, j, float(doseimg2[j,i]))

initial_transform = sitk.CenteredTransformInitializer(fixedimg, 
                                                      movingimg, 
                                                      sitk.Euler2DTransform(), 
                                                      sitk.CenteredTransformInitializerFilter.GEOMETRY)

#moving_resampled = sitk.Resample(movingimg, fixedimg, initial_transform, sitk.sitkLinear, 0.0, movingimg.GetPixelID())


# Real registration:
registration_method = sitk.ImageRegistrationMethod()

# Similarity metric settings.
registration_method.SetMetricAsMattesMutualInformation(numberOfHistogramBins=50)
registration_method.SetMetricSamplingStrategy(registration_method.RANDOM)
registration_method.SetMetricSamplingPercentage(0.01)

registration_method.SetInterpolator(sitk.sitkLinear)

# Optimizer settings.
registration_method.SetOptimizerAsGradientDescent(learningRate=1.0, numberOfIterations=100, convergenceMinimumValue=1e-6, convergenceWindowSize=10)
registration_method.SetOptimizerScalesFromPhysicalShift()

# Setup for the multi-resolution framework.            
registration_method.SetShrinkFactorsPerLevel(shrinkFactors = [4,2,1])
registration_method.SetSmoothingSigmasPerLevel(smoothingSigmas=[2,1,0])
registration_method.SmoothingSigmasAreSpecifiedInPhysicalUnitsOn()

# Don't optimize in-place, we would possibly like to run this cell multiple times.
registration_method.SetInitialTransform(initial_transform, inPlace=False)

final_transform = registration_method.Execute(sitk.Cast(fixedimg, sitk.sitkFloat32), 
                                              sitk.Cast(movingimg, sitk.sitkFloat32))

finalimg = sitk.Resample(movingimg, fixedimg, final_transform, sitk.sitkLinear, 0.0, movingimg.GetPixelID())


doseimg = sitk.GetArrayFromImage(finalimg)

displayImage(doseimg, finalimg.GetWidth(), finalimg.GetHeight(), m_imgPlotWidth)
